# Python with PostgreSQL & PostGIS

<span style="color: blue;">Note: Please always run the complete Jupyter Notebook from the beginning, as object names such as 'sql' and 'gdf' are reused in the code cells.</span>

## Libraries and Settings

In [1]:
# Libraries
import os
import folium
import pandas as pd
import geopandas as gpd
from sqlalchemy import create_engine, text

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

print(os.getcwd())

/workspaces/python_postgresql_postgis


## Create database connection

In [2]:
# Set up database connection
user = "pgadmin"
password = "geheim"
host = "localhost"
port = "5432"
database = "osm_switzerland"

# Create Connection URL
db_connection_url = "postgresql://" + user + ":" + password +\
                    "@" + host + ":" + port + "/" + database

# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Test database connection
with engine.connect() as connection:
    result = connection.execute(text('SELECT current_database()'))
    print(result.fetchone())

# Dispose the engine
engine.dispose()

('osm_switzerland',)


## List tables in database

In [3]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Open a connection
with engine.connect() as connection:

    # Execute the query
    result = connection.execute(text("""SELECT table_name
                                        FROM information_schema.tables
                                        WHERE table_schema = 'public';"""))
    
    # Fetch and print the results
    for row in result:
        print(row[0])

# Dispose the engine
engine.dispose()

geography_columns
geometry_columns
spatial_ref_sys
planet_osm_point
planet_osm_line
planet_osm_polygon
planet_osm_roads


## Show columns and data types of selected table

In [4]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Specify your table name
table_name = 'planet_osm_polygon'

# Query to get column information
query = f"""SELECT column_name, data_type 
        FROM information_schema.columns 
        WHERE table_name = '{table_name}'"""

# Execute the query and read the result into a DataFrame
df = pd.read_sql(query, engine)

# Dispose the engine
engine.dispose()

# Print the DataFrame
df

column_name     data_type
0             osm_id        bigint
1            z_order       integer
2           way_area          real
3                way  USER-DEFINED
4   addr:housenumber          text
..               ...           ...
68              wood          text
69         tracktype          text
70            access          text
71    addr:housename          text
72       addr:street          text

[73 rows x 2 columns]

## Query: Select buildings for which full address is available in defined zip code areas

In [7]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query 
sql = """SELECT
                p.osm_id,
                p."addr:street",
                p."addr:housenumber",
                p."addr:city",
                p."addr:postcode",
                p.building,
                st_transform(p.way, 4326) AS geom
        FROM
                public.planet_osm_polygon AS p
        WHERE
                p."addr:street" IS NOT NULL
                AND p."addr:housenumber" IS NOT NULL
                AND p."addr:city" IS NOT NULL
                AND p."addr:postcode" IN ('8001', '8002', '8055')"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id           addr:street addr:housenumber addr:city  \
0      10210723  Birmensdorferstrasse              497    Zürich   
1      10677874    Stadelhoferstrasse                8    Zürich   
2      10696509           Sihlstrasse               71    Zürich   
3      23454701  Birmensdorferstrasse              501    Zürich   
4      23734233      Scheideggstrasse               65    Zürich   
...         ...                   ...              ...       ...   
3743  371878836         Brunaustrasse               91    Zürich   
3744  371878839        Allmendstrasse               5a    Zürich   
3745  373233344   Stampfenbachstrasse                8    Zürich   
3746  373277524          Freieckgasse                7    Zürich   
3747  373757633          Bederstrasse              101    Zürich   

     addr:postcode       building  \
0             8055       hospital   
1             8001  train_station   
2             8001            yes   
3             8055       hospital   
4             8002            yes   
...            ...            ...   
3743          8002            yes   
3744          8002            yes   
3745          8001            yes   
3746          8001          house   
3747          8002     apartments   

                                                   geom  
0     POLYGON ((8.49657 47.36587, 8.49675 47.36551, ...  
1     POLYGON ((8.54815 47.36668, 8.5483 47.36657, 8...  
2     POLYGON ((8.53237 47.37213, 8.53306 47.37186, ...  
3     POLYGON ((8.4948 47.36607, 8.49496 47.36575, 8...  
4     POLYGON ((8.52945 47.35397, 8.52948 47.35397, ...  
...                                                 ...  
3743  POLYGON ((8.5257 47.3529, 8.52585 47.35277, 8....  
3744  POLYGON ((8.52504 47.35294, 8.52517 47.35283, ...  
3745  POLYGON ((8.54378 47.37785, 8.5438 47.37784, 8...  
3746  POLYGON ((8.54572 47.36742, 8.54582 47.36732, ...  
3747  POLYGON ((8.52601 47.36147, 8.52602 47.36143, ...  

[3748 rows x 7 columns]

## Show selected features on map

<span style="color: blue;">Note the popup field in the map, which has been added to provide additional information about buildings.</span>

<span style="color: blue;">Example of alternative background maps (maptiles) are:</span>
- <span style="color: blue;">EsriWorldImagery</span>
- <span style="color: blue;">EsriWorldTopoMap</span>
- <span style="color: blue;">EsriWorldGrayCanvas</span>
- <span style="color: blue;">CartoDBDarkMatter</span>
- <span style="color: blue;">CartoDBPositron</span>


In [8]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=15,
               tiles='EsriWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='geojson',
    weight=0.5,
    fill_color='greenyellow',
    fillOpacity=0.8,
    popup=folium.GeoJsonPopup(fields=['addr:street',
                                      'addr:housenumber',
                                      'addr:city',
                                      'addr:postcode',
                                      'building'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select coffee stores in Switzerland

In [9]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            h.osm_id,
            h.shop,
            h.name,
            ST_Transform(h.way, 4326) AS geom
        FROM planet_osm_point h
        WHERE h.shop = 'coffee';"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id    shop                                name  \
0     1420063327  coffee                           Esperanza   
1     1784568574  coffee                      Landolt Kaffee   
2     2411403524  coffee             Goldcastle Tea & Coffee   
3     2582129127  coffee                         Don Camillo   
4     2647639693  coffee                              Tchibo   
..           ...     ...                                 ...   
121  10967856734  coffee                            Beanbank   
122  10990063195  coffee                  Suter's Petit Café   
123  10992872554  coffee  Barista Academy Turm Kaffee Zürich   
124  11577208880  coffee                           Mingmatic   
125  12088350770  coffee                Stocker's & Kofi bar   

                         geom  
0    POINT (7.02052 46.61817)  
1     POINT (9.0631 47.10036)  
2    POINT (6.95454 47.07048)  
3    POINT (8.17646 47.39941)  
4    POINT (9.04491 47.46487)  
..                        ...  
121  POINT (8.53654 47.36939)  
122   POINT (7.99496 47.1236)  
123  POINT (8.45302 47.39873)  
124  POINT (8.11102 47.17484)  
125  POINT (8.51762 47.17204)  

[126 rows x 4 columns]

## Show selected features on map

In [10]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'shop'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all supermarkets in a distance of 1000m around the central station in the city of Winterthur.

<span style="color: blue;">Note:</span>

<span style="color: blue;">For each supermarket, the distance to the central station in meters is calculated and stored as new column 'distance_meters'.</span>

<span style="color: blue;">In addition, a popup field was added to the map, allowing users to view detailed information about each selected feature when they click on it.</span>

<span style="color: blue;">The WGS84 (World Geodetic System 1984) coordinates in ST_MakePoint(LON, LAT) were derived from: https://tools.retorte.ch/map.</span>


In [11]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)  

# Define SQL query
sql = """SELECT
            p.osm_id,
            p.shop,
            p.name,
            ST_Distance(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography
            ) AS distance_meters,
            ST_TRANSFORM(p.way, 4326) AS geom
        FROM
            planet_osm_point AS p
        WHERE
            p.shop = 'supermarket'
            AND ST_DWithin(
                ST_Transform(p.way, 4326)::geography,
                -- Central station coordinates
                ST_SetSRID(ST_MakePoint(8.72397, 47.50031), 4326)::geography,
                1000
            )
        ORDER BY distance_meters;"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine)

# Dispose the engine
engine.dispose()

# Print the GeoDataFrame
gdf


osm_id         shop                          name  distance_meters  \
0   706203439  supermarket                          Coop       159.883419   
1  4109460421  supermarket                     Asia Shop       162.391281   
2  3831772784  supermarket                        Migros       247.578208   
3  7380954145  supermarket                      Alnatura       256.838011   
4  4095400190  supermarket                          ALDI       274.275393   
5  4125136758  supermarket  Tandoor Indischer Supermarkt       290.212664   
6  4095400136  supermarket                        Denner       316.354037   
7   709022324  supermarket               Claro Weltladen       441.129317   
8  4058248551  supermarket                        Migros       600.117307   
9  3441033104  supermarket                L'Ultimo Bacio       680.202961   

                       geom  
0  POINT (8.72594 47.50085)  
1  POINT (8.72208 47.50101)  
2  POINT (8.72115 47.49916)  
3  POINT (8.72074 47.49958)  
4   POINT (8.72476 47.4979)  
5  POINT (8.72017 47.50073)  
6  POINT (8.72036 47.49886)  
7  POINT (8.72912 47.49842)  
8  POINT (8.73193 47.50012)  
9  POINT (8.73299 47.49999)

## Show selected features on map

In [12]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=16, 
               tiles='ESRIWorldImagery')

# Map settings
folium.GeoJson(
    gdf,
    name='map',
    popup=folium.GeoJsonPopup(fields=['name', 'distance_meters'])
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

## Query: Select all roads classified as 'motorway' and create a 5000m buffer around these roads.

In [13]:
# Create SQLAlchemy Engine
engine = create_engine(db_connection_url)

# Define SQL query (major roads)
sql = """-- Create buffer around major roads
        SELECT 
            1 as group_id,
            ST_TRANSFORM(ST_UNION(ST_Buffer(p.way::geometry, 5000)), 4326) AS geom
        FROM public.planet_osm_roads AS p
        WHERE
            highway = 'motorway';"""

# Query the database and store the result in a GeoDataFrame
gdf = gpd.GeoDataFrame.from_postgis(sql, engine, geom_col='geom')

# Dispose the engine
engine.dispose()

## Show selected features on map

In [14]:
# Ensure the GeoDataFrame has the correct projection (EPSG:4326)
if gdf.crs is None:
    gdf.set_crs(epsg=4326, inplace=True)
else:
    pass

# Calculate the mean longitude and latitude for the map center
centroids = gdf.geometry.centroid
lon = centroids.x.mean()
lat = centroids.y.mean()

# Initialize the map
m = folium.Map(location=[lat, lon], 
               zoom_start=9, 
               tiles='EsriWorldTopoMap')

# Map settings
folium.GeoJson(
    gdf,
    name='map'
).add_to(m)

folium.LayerControl().add_to(m)

# Plot map
m

### Jupyter notebook --footer info-- (please always provide this at the end of each notebook)

In [15]:
import os
import platform
import socket
from platform import python_version
from datetime import datetime

print('-----------------------------------')
print(os.name.upper())
print(platform.system(), '|', platform.release())
print('Datetime:', datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print('Python Version:', python_version())
print('-----------------------------------')

-----------------------------------
POSIX
Linux | 6.8.0-1021-azure
Datetime: 2025-03-13 19:55:58
Python Version: 3.12.1
-----------------------------------
